# Ghost of Departed Proofs

> Juan Pablo Yamamoto  
> jpyamamoto\[at\]ciencias.unam.mx  
> Lógica Computacional II. Semestre 2025-1.

## Requisitos Previos

In [1]:
{-# LANGUAGE TypeOperators #-}
{-# LANGUAGE LiberalTypeSynonyms #-}
{-# LANGUAGE ImpredicativeTypes #-}
{-# LANGUAGE PolyKinds #-}
{-# LANGUAGE MultiParamTypeClasses #-}

## Prueba

Codificamos las pruebas como algo con un constructor `QED` y los axiomas como simplemente una construcción de la prueba.

In [2]:
data Prueba (term :: k) = QED

axioma :: Prueba p
axioma = QED

## Términos de la Lógica

La codificación de los términos se hace al nivel de tipos: no estamos usando el lenguaje de programación, **estamos utilizando el verificador de tipos**.

**Valores de verdad:**

In [3]:
data Verdadero
data Falso

**Operadores "básicos":**

In [4]:
data Conjuncion p q
data Disyuncion p q
data Implicacion p q

**Operadores "derivados":**

In [5]:
type No p = Implicacion p Falso
type Equivalencia p q = Conjuncion (Implicacion p q) (Implicacion q p)

**Cuantificadores:**

In [6]:
data Existe x p
data ParaTodo x p

**Alias para simplificar la notación:**

In [7]:
type p ∧ q = Conjuncion p q
type p ∨ q = Disyuncion p q
type p → q = Implicacion p q
type p ↔ q = Equivalencia p q

infixl 5 ∨
infixl 5 ∧
infixr 4 →
infixr 3 ↔

**Notación de secuentes:**

In [8]:
type p ⊢ q = p -> q
infixr 2 ⊢

type p ∴ q = p -> q
infixr 1 ∴

## Reglas de Deducción Intuicionista

**Constantes de verdad:**

In [9]:
trivial :: Prueba Verdadero
trivial = axioma

exfalso :: Prueba Falso ∴ Prueba a
exfalso _ = axioma

**Conjunción:**

In [10]:
constructor :: (Prueba a, Prueba b) ∴ Prueba (a ∧ b)
constructor _ = axioma

first :: Prueba (a ∧ b) ∴ Prueba a
first _ = axioma

second :: Prueba (a ∧ b) ∴ Prueba b
second _ = axioma

**Disyunción:**

In [11]:
left :: Prueba a ∴ Prueba (a ∨ b)
left _ = axioma

right :: Prueba b ∴ Prueba (a ∨ b)
right _ = axioma

cases :: (Prueba (a ∨ b), Prueba a ⊢ Prueba c, Prueba b ⊢ Prueba c) ∴ Prueba c
cases (_, _, _) = axioma

**Implicación:**

In [12]:
intro :: (Prueba a ⊢ Prueba b) ∴ Prueba (a → b)
intro _ = axioma

apply :: (Prueba (a → b), Prueba a) ∴ Prueba b
apply (_, _) = axioma

**Cuantificador universal:**

In [13]:
generalize :: (forall c. Prueba (p c)) ∴ Prueba (ParaTodo x (p x))
generalize _ = axioma

specialize :: Prueba (ParaTodo x (p x)) ∴ Prueba (p c)
specialize _ = axioma

**Cuantificador existencial:**

In [14]:
use :: Prueba (p c) ∴ Prueba (Existe x (p x))
use _ = axioma

destruct :: (Prueba (Existe x (p x)), (forall c. Prueba (p c)) ⊢ Prueba q) ∴ Prueba q
destruct _ = axioma

## Reglas de Deducción Clásica

Definimos una clase que no tiene métodos, simplemente funciona como un contexto para restringir el uso de las reglas clásicas.

In [15]:
class Clasicamente

**Regla para caracterizar la lógica clásica:**

In [16]:
absurd :: Clasicamente => (Prueba (No a) ⊢ Prueba Falso) ∴ Prueba a
absurd _ = axioma

## Ejemplos

In [17]:
ejemplo1 :: (Prueba a, Prueba ((b → a) → c)) ⊢ Prueba (d → c)
ejemplo1 (a, bac) = intro (\d -> apply (bac, intro (\b -> a)))

Line 2: Use const
Found:
\ b -> a
Why not:
const a

In [18]:
ejemplo2 :: Clasicamente => Prueba ((No (p → q)) → p)
ejemplo2 = intro (\nopq -> absurd (\nop -> apply (nopq, intro (\p -> exfalso (apply (nop, p))))))

Line 1: Redundant bracket
Found:
(No (p -> q)) -> p
Why not:
No (p -> q) -> p